In [1]:
import numpy as np
import pandas as pd
import os
from datetime import datetime, timedelta
import matplotlib.pyplot as plt
import alpaca_trade_api as tradeapi
import hvplot.pandas
%matplotlib inline

In [2]:
pd.set_option('display.max_rows', 3200)
pd.set_option('display.max_columns', 50)
pd.set_option('display.width', 1000)

In [3]:
etf_portfolio = pd.DataFrame(index=["purchase_date", "weights", "seed_money", "num_shares"],
                            columns = ['XLB', 'XLC', 'XLE', 'XLF', 'XLI', 'XLK', 'XLP', 'XLRE', 'XLU', 'XLV',
       'XLY'])
etf_portfolio

XLB  XLC  XLE  XLF  XLI  XLK  XLP XLRE  XLU  XLV  XLY
purchase_date  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN
weights        NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN
seed_money     NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN
num_shares     NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN

In [4]:
df = pd.read_csv("./Resources/etf_daily_prices.csv", index_col='Date', parse_dates=True, infer_datetime_format=True)

In [5]:
df = df.loc['2018-06-29':]
df

XLB      XLC      XLE      XLF      XLI       XLK      XLP     XLRE      XLU       XLV       XLY
Date                                                                                                            
2018-06-29  58.0700  49.4700  75.9800  26.5700  71.6400   69.4300  51.5100  32.7100  51.9400   83.4400  109.2900
2018-07-02  57.7700  49.8400  74.7500  26.7200  71.7600   70.1000  51.2300  32.5300  52.3300   83.7000  109.4500
2018-07-03  57.6700  49.1890  75.3700  26.4700  71.5600   69.2700  51.3600  32.7100  52.4800   83.9600  108.8900
2018-07-05  58.1700  49.9799  75.2100  26.5400  71.8900   70.2400  52.0800  33.1400  52.7900   84.8200  109.4500
2018-07-06  58.4400  50.7700  75.6800  26.6600  72.1500   71.0500  52.2300  33.2700  53.1800   86.0200  110.3100
2018-07-09  58.9900  51.0700  76.8100  27.2900  73.4700   71.6000  52.0000  32.9700  51.5300   86.5900  111.6200
2018-07-10  59.4600  51.0390  77.3800  27.1700  73.7100   71.7900  52.6400  33.1300  52.0300   86.9600  111.8500
2018-07-11  58.4700  50.9700  75.7100  27.0400  72.5300   71.4200  52.4600  33.0200  52.4900   86.2600  111.6100
2018-07-12  58.6100  51.7700  75.8400  27.0900  73.3300   72.6200  52.4100  33.1000  52.5200   87.2500  112.3500
2018-07-13  58.5900  51.6900  76.2550  26.9600  73.7700   72.5600  52.7300  33.0100  52.5500   87.4400  112.6200
2018-07-16  58.1200  51.5400  75.3600  27.4550  73.4500   72.3600  52.4800  32.8200  52.4800   86.8500  112.8500
2018-07-17  58.8900  51.5400  75.1100  27.5000  73.7350   72.9000  52.9200  32.6100  52.4500   87.3400  112.9700
2018-07-18  58.9100  51.4000  75.1300  27.9200  74.5600   72.8000  52.5400  32.4700  52.1800   87.4000  112.8800
2018-07-19  58.5200  51.0400  75.1300  27.5100  74.5300   72.5550  52.5500  32.7950  52.6700   86.9200  112.6500
2018-07-20  58.3000  50.8700  74.8700  27.5700  74.4400   72.5500  52.8500  32.5000  52.2800   86.7400  112.1500
2018-07-23  57.9900  51.0400  74.5700  27.9300  73.9750   72.9000  52.5500  32.4200  51.9300   86.9500  112.0400
2018-07-24  58.7400  51.4400  75.5100  28.0100  74.3200   73.3100  52.6200  32.3100  52.1000   87.7300  111.7100
2018-07-25  59.1800  51.8100  76.2100  28.0950  75.3500   74.2100  52.9900  32.6300  52.2500   88.7600  112.5200
2018-07-26  59.5100  49.8562  76.9800  28.0550  75.9900   73.0900  53.3200  32.7450  52.8400   88.5800  111.9200
2018-07-27  59.3000  48.9100  76.6300  28.1300  75.9800   71.8200  53.3800  32.4500  52.6400   87.9400  111.6600
2018-07-30  59.1800  48.1700  77.3000  28.1400  75.2700   70.7400  53.3200  32.4300  52.3300   88.0300  110.7800
2018-07-31  59.7100  48.4600  77.0600  27.9500  76.8600   70.9100  53.5600  33.0400  52.8700   88.9200  111.2600
2018-08-01  59.1300  48.2600  76.0300  27.9500  75.8900   71.5400  53.0900  33.2800  52.4400   88.9600  110.7600
2018-08-02  58.7100  48.5800  75.6300  27.9600  75.7700   72.4400  53.6650  33.1000  52.7300   89.2700  111.4500
2018-08-03  59.2800  48.9100  75.2600  28.1100  75.8300   72.7100  54.3000  33.5350  53.2800   89.8200  111.8200
2018-08-06  59.2800  49.3700  75.5400  28.2500  75.9350   73.1400  54.3100  33.4650  53.3500   89.9600  112.5900
2018-08-07  59.4500  49.4500  76.0700  28.3800  76.4800   73.3900  54.0000  33.4100  53.2500   89.9600  113.1000
2018-08-08  59.2500  49.4200  75.5200  28.4600  76.1500   73.5800  53.5900  33.2100  52.9800   90.1000  113.2400
2018-08-09  59.5400  49.6900  74.8100  28.3100  75.7400   73.6100  53.4400  33.2600  53.2100   90.0000  113.6600
2018-08-10  58.6900  49.2700  75.2300  27.9800  75.1300   73.0400  53.2500  32.9300  52.9900   89.6400  112.7100
2018-08-13  58.1000  49.2000  74.3100  27.7000  74.7500   72.9500  53.2300  32.9300  53.0600   89.6700  112.1600
2018-08-14  58.5700  49.5500  74.5100  27.9400  75.2400   73.4100  53.5900  33.0500  53.1900   90.0800  113.2500
2018-08-15  57.6400  48.8600  71.9100  27.7500  74.8800   72.7500  53.8100  33.3400  53.6100   89.9400  111.8600
2018-08-16  58.0100  48.8400  72.4300  28.1000  75.8000   73.

In [6]:
df.isnull().sum()

XLB     0
XLC     0
XLE     0
XLF     0
XLI     0
XLK     0
XLP     0
XLRE    0
XLU     0
XLV     0
XLY     0
dtype: int64

In [7]:
weight_df = pd.read_csv("./Resources/SOROS_weight_data.csv", index_col = 'Date', parse_dates=True, infer_datetime_format=True)
weight_df

XLB        XLC       XLE        XLF       XLI        XLK       XLP       XLRE        XLU       XLV        XLY
Date                                                                                                                          
2018-06-29       NaN  16.658948  4.208955  33.514748  2.246996  17.012898  0.336696   7.915742   5.249415  2.283925  10.571677
2018-09-28       NaN  23.783240  6.173178  20.565896  0.861520  14.394842  5.157079  10.835662   3.792365  3.604098  10.832121
2018-12-31  1.014936  23.826734  3.287115  20.695024  0.390614  14.271199  7.857675  11.892216   5.299985  0.788728  10.675774
2019-03-29  0.100412  23.277593  4.402428  22.215266  0.813898  18.235588  5.955715   9.972997   2.132356  2.687723  10.206025
2019-06-28  1.201778  21.241607  4.063839  28.319342  1.528953  10.639758  5.524076  11.538165   0.929315  4.144257  10.868911
2019-09-30  0.937375  23.688684  6.912750  14.917438  2.025376   9.866314  4.012086  15.422419   1.513530  8.356620  12.347405
2019-12-31  0.801096  26.334843  6.898420  16.884634  2.545869  13.809884  6.464359   9.908050   1.303488  5.930061   9.119296
2020-03-31  1.323902  32.825236  2.373221  12.075781  3.754598  13.419083  0.054690   7.792035   5.241950  8.261850  12.877655
2020-06-30  0.767883  16.904551  1.614048  37.781081  3.514545   7.892766  3.180200   4.151718  11.416067  3.055979   9.721162

In [8]:
weight_df = weight_df.loc['2018-06-29':]
weight_df

XLB        XLC       XLE        XLF       XLI        XLK       XLP       XLRE        XLU       XLV        XLY
Date                                                                                                                          
2018-06-29       NaN  16.658948  4.208955  33.514748  2.246996  17.012898  0.336696   7.915742   5.249415  2.283925  10.571677
2018-09-28       NaN  23.783240  6.173178  20.565896  0.861520  14.394842  5.157079  10.835662   3.792365  3.604098  10.832121
2018-12-31  1.014936  23.826734  3.287115  20.695024  0.390614  14.271199  7.857675  11.892216   5.299985  0.788728  10.675774
2019-03-29  0.100412  23.277593  4.402428  22.215266  0.813898  18.235588  5.955715   9.972997   2.132356  2.687723  10.206025
2019-06-28  1.201778  21.241607  4.063839  28.319342  1.528953  10.639758  5.524076  11.538165   0.929315  4.144257  10.868911
2019-09-30  0.937375  23.688684  6.912750  14.917438  2.025376   9.866314  4.012086  15.422419   1.513530  8.356620  12.347405
2019-12-31  0.801096  26.334843  6.898420  16.884634  2.545869  13.809884  6.464359   9.908050   1.303488  5.930061   9.119296
2020-03-31  1.323902  32.825236  2.373221  12.075781  3.754598  13.419083  0.054690   7.792035   5.241950  8.261850  12.877655
2020-06-30  0.767883  16.904551  1.614048  37.781081  3.514545   7.892766  3.180200   4.151718  11.416067  3.055979   9.721162

In [9]:
dollar_value = pd.DataFrame(index= df.index, columns=df.columns)

In [10]:
initial_capital = 100000
# Setting null value if not purchased at the start date.
for j in range(len(weight_df.index)):
    for i in range(len(df.index)):
       
        for index, col in df.iterrows():
            if  j == 0 and df.index[i] == weight_df.index[j]:
                etf_portfolio.loc['purchase_date'] = weight_df.index[j].date()
                etf_portfolio.loc['weights'] = weight_df.loc[weight_df.index[j]]
                etf_portfolio.loc['seed_money'] = etf_portfolio.loc['weights'] * initial_capital / 100
                etf_portfolio.loc["num_shares"] = etf_portfolio.loc["seed_money"] / df.loc[df.index[i]]  
                
                # dollar value calculation
                value_by_stock = df.loc[df.index[i]] * etf_portfolio.loc["num_shares"]
                dollar_value.loc[dollar_value.index[i]] = value_by_stock
            
            elif j == 0 and df.index[i] != weight_df.index[j]:
                value_by_stock = df.loc[df.index[i]] * etf_portfolio.loc["num_shares"]
                dollar_value.loc[dollar_value.index[i]] = value_by_stock
                
            elif j != 0 and df.index[i] == weight_df.index[j]:
                etf_portfolio.index.insert(-1, f"rebalacning_date_{j}")
                etf_portfolio.index.insert(-1, f"weights_{j}")
                etf_portfolio.index.insert(-1, f"seed_money_{j}")
                etf_portfolio.index.insert(-1, f"num_shares_{j}")
                
                etf_portfolio.loc[f"rebalacning_date_{j}"] = weight_df.index[j].date()
                etf_portfolio.loc[f'weights_{j}'] = weight_df.loc[weight_df.index[j]]
                total_portfolio_value = dollar_value.iloc[i].sum()
                etf_portfolio.loc[f"seed_money_{j}"] = etf_portfolio.loc[f'weights_{j}'] * total_portfolio_value / 100
                etf_portfolio.loc[f"num_shares_{j}"] = etf_portfolio.loc[f"seed_money_{j}"] / df.loc[df.index[i]]  
                
                # dollar value calculation
                value_by_stock = df.loc[df.index[i]] * etf_portfolio.loc[f"num_shares_{j}"]
                dollar_value.loc[dollar_value.index[i]] = value_by_stock
                
            elif j!= 0 and df.index[i] > weight_df.index[j]:
                value_by_stock = df.loc[df.index[i]] * etf_portfolio.loc[f"num_shares_{j}"]
                dollar_value.loc[dollar_value.index[i]] = value_by_stock  

In [11]:
etf_portfolio

XLB         XLC         XLE         XLF         XLI         XLK         XLP        XLRE         XLU         XLV         XLY
purchase_date       2018-06-29  2018-06-29  2018-06-29  2018-06-29  2018-06-29  2018-06-29  2018-06-29  2018-06-29  2018-06-29  2018-06-29  2018-06-29
weights                    NaN     16.6589     4.20896     33.5147       2.247     17.0129    0.336696     7.91574     5.24941     2.28392     10.5717
seed_money                 NaN     16658.9     4208.96     33514.7        2247     17012.9     336.696     7915.74     5249.41     2283.92     10571.7
num_shares                 NaN     336.748     55.3956     1261.38     31.3651     245.037     6.53652     241.998     101.067     27.3721     96.7305
rebalacning_date_1  2018-09-28  2018-09-28  2018-09-28  2018-09-28  2018-09-28  2018-09-28  2018-09-28  2018-09-28  2018-09-28  2018-09-28  2018-09-28
weights_1                  NaN     23.7832     6.17318     20.5659     0.86152     14.3948     5.15708     10.8357     3.79237      3.6041     10.8321
seed_money_1               NaN     24708.2     6413.26     21365.7     895.025     14954.7     5357.64     11257.1     3939.86     3744.27     11253.4
num_shares_1               NaN     504.455     84.6747     774.963     11.4191     198.549     99.3628     345.097     74.7885     39.3677     96.0351
rebalacning_date_2  2018-12-31  2018-12-31  2018-12-31  2018-12-31  2018-12-31  2018-12-31  2018-12-31  2018-12-31  2018-12-31  2018-12-31  2018-12-31
weights_2              1.01494     23.8267     3.28712      20.695    0.390614     14.2712     7.85768     11.8922     5.29999    0.788728     10.6758
seed_money_2           906.691     21285.6     2936.54     18487.9     348.954     12749.2     7019.64     10623.9     4734.73     704.608     9537.18
num_shares_2           18.0403     518.528     51.4723     780.408     5.44815     206.984     138.865     343.656     89.7239     8.19982     96.8634
rebalacning_date_3  2019-03-29  2019-03-29  2019-03-29  2019-03-29  2019-03-29  2019-03-29  2019-03-29  2019-03-29  2019-03-29  2019-03-29  2019-03-29
weights_3             0.100412     23.2776     4.40243     22.2153    0.813898     18.2356     5.95571       9.973     2.13236     2.68772      10.206
seed_money_3           102.099     23668.6     4476.39     22588.5     827.571     18541.9     6055.77     10140.5     2168.18     2732.87     10377.5
num_shares_3           1.83995     506.173     67.7009     878.587     11.0299     250.567     107.927     279.971     37.2667     29.7861     91.1504
rebalacning_date_4  2019-06-28  2019-06-28  2019-06-28  2019-06-28  2019-06-28  2019-06-28  2019-06-28  2019-06-28  2019-06-28  2019-06-28  2019-06-28
weights_4              1.20178     21.2416     4.06384     28.3193     1.52895     10.6398     5.52408     11.5382    0.929315     4.14426     10.8689
seed_money_4            1278.9     22604.7     4324.62     30136.6     1627.07     11322.5     5878.57     12278.6     988.951      4410.2     11566.4
num_shares_4           21.8578     459.352     67.8905     1091.91     21.0352     144.938     101.232     333.839     16.5681     47.6367     97.0335
rebalacning_date_5  2019-09-30  2019-09-30  2019-09-30  2019-09-30  2019-09-30  2019-09-30  2019-09-30  2019-09-30  2019-09-30  2019-09-30  2019-09-30
weights_5             0.937375     23.6887     6.91275     14.9174     2.02538     9.86631     4.01209     15.4224     1.51353     8.35662     12.3474
seed_money_5           1015.76     25669.5     7490.79     16164.8     2194.74     10691.3     4347.58       16712     1640.09      9055.4     13379.9
num_shares_5           17.4619     518.367     126.576     576.904     28.2645     132.779     70.7959      424.81     25.3413      100.47     110.862
rebalacning_date_6  2019-12-31  2019-12-31  2019-12-31  2019-12-31  2019-12-31  2019-12-31  2019-12-31  2019-12-31  2019-12-31  2019-12-31  2019-12-31
weights_6             0.801096     26.3348     6.89842     16.8846     2.54587     13.8099     6.4643

In [12]:
dollar_value.head(100)

XLB      XLC      XLE      XLF      XLI      XLK      XLP     XLRE      XLU      XLV      XLY
Date                                                                                                     
2018-06-29  NaN  16658.9  4208.96  33514.7     2247  17012.9  336.696  7915.74  5249.41  2283.92  10571.7
2018-07-02  NaN  16783.5  4140.82    33704  2250.76  17177.1  334.866  7872.18  5288.83  2291.04  10587.2
2018-07-03  NaN  16564.3  4175.16  33388.6  2244.49  16973.7  335.716  7915.74  5303.99  2298.16    10533
2018-07-05  NaN  16830.7   4166.3  33476.9  2254.84  17211.4  340.422   8019.8  5335.32   2321.7  10587.2
2018-07-06  NaN  17096.7  4192.34  33628.3  2262.99  17409.9  341.403  8051.26  5374.74  2354.54  10670.3
2018-07-09  NaN  17197.7  4254.93  34422.9  2304.39  17544.6  339.899  7978.66  5207.98  2370.15  10797.1
2018-07-10  NaN  17187.3  4286.51  34271.6  2311.92  17591.2  344.083  8017.38  5258.51  2380.27  10819.3
2018-07-11  NaN  17164.1     4194  34107.6  2274.91  17500.5  342.906  7990.76     5305  2361.11  10796.1
2018-07-12  NaN  17433.5   4201.2  34170.7     2300  17794.6  342.579  8010.12  5308.03  2388.21  10867.7
2018-07-13  NaN  17406.5  4224.19  34006.7   2313.8  17779.9  344.671  7988.34  5311.07  2393.41  10893.8
2018-07-16  NaN    17356  4174.61  34631.1  2303.77  17730.9  343.037  7942.36  5303.99  2377.26    10916
2018-07-17  NaN    17356  4160.76  34687.8  2312.71  17863.2  345.913  7891.54  5300.96  2390.68  10927.6
2018-07-18  NaN  17308.9  4161.87  35217.6  2338.58  17838.7  343.429  7857.66  5273.67  2392.32  10918.9
2018-07-19  NaN  17187.6  4161.87  34700.4  2337.64  17778.6  343.494  7936.31  5323.19  2379.18  10896.7
2018-07-20  NaN  17130.4  4147.47  34776.1  2334.82  17777.4  345.455  7864.92  5283.78  2374.25  10848.3
2018-07-23  NaN  17187.6  4130.85  35230.2  2320.23  17863.2  343.494  7845.56   5248.4     2380  10837.7
2018-07-24  NaN  17322.3  4182.92  35331.1  2331.05  17963.6  343.952  7818.94  5265.59  2401.35  10805.8
2018-07-25  NaN  17446.9   4221.7  35438.3  2363.36  18184.2   346.37  7896.38  5280.75  2429.54  10884.1
2018-07-26  NaN    16789  4264.35  35387.9  2383.43  17909.7  348.527  7924.21  5340.37  2424.62  10826.1
2018-07-27  NaN  16470.4  4244.96  35482.5  2383.12  17598.5   348.92  7852.82  5320.16   2407.1  10800.9
2018-07-30  NaN  16221.2  4282.08  35495.1  2360.85  17333.9  348.527  7847.98  5288.83  2409.56  10715.8
2018-07-31  NaN  16318.8  4268.78  35255.4  2410.72  17375.6  350.096   7995.6  5343.41  2433.92  10762.2
2018-08-01  NaN  16251.5  4211.73  35255.4   2380.3  17529.9  347.024  8053.68  5299.95  2435.02  10713.9
2018-08-02  NaN  16359.2  4189.57  35268.1  2376.53  17750.5  350.782  8010.12  5329.26   2443.5  10780.6
2018-08-03  NaN  16470.4  4169.07  35457.3  2378.42  17816.6  354.933  8115.39  5384.84  2458.56  10816.4
2018-08-06  NaN  16625.3  4184.58  35633.9  2381.71    17922  354.999  8098.45  5391.92  2462.39  10890.9
2018-08-07  NaN  16652.2  4213.94  35797.8   2398.8  17983.2  352.972  8085.14  5381.81  2462.39  10940.2
2018-08-08  NaN  16642.1  4183.47  35898.7  2388.45  18029.8  350.292  8036.74  5354.52  2466.22  10953.8
2018-08-09  NaN    16733  4144.14  35709.5  2375.59  18037.2  349.312  8048.84  5377.77  2463.49  10994.4
2018-08-10  NaN  16591.6  4167.41  35293.3  2356.46  17897.5   348.07  7968.98  5355.53  2453.63  10902.5
2018-08-13  NaN    16568  4116.44  34940.1  2344.54  17875.4  347.939  7968.98  5362.61  2454.45  10849.3
2018-08-14  NaN  16685.9  4127.52  35242.8  2359.91  17988.1  350.292  7998.02  5375.75  2465.68  10954.7
2018-08-15  NaN  16453.5   3983.5  35003.2  2348.62  17826.4   351.73   8068.2   5418.2  2461.84  10820.3
2018-08-16  NaN  16446.8   4012.3  35444.7  2377.47    17895   357.09  8133.54  5482.88  2485.38  10872.5
2018-08-17  NaN  16369.3  4023.38  35520.3  2392.22  17931.8  359.705  8208.56  5509.16  2494.14  10883.1
2018-08-20  NaN  16382.8  4049.97  35633.9  2407.59  17902.4  359.509  8214.61  5489.95  2

In [13]:
total_portfolio_value = dollar_value.iloc[-1].sum()
total_portfolio_value

116951.11472154126

In [14]:
portfolio_value = dollar_value.copy()
portfolio_value["Daily Total"] = round(dollar_value[etf_portfolio.columns].sum(axis=1), 2)
portfolio_value

XLB      XLC      XLE      XLF      XLI      XLK      XLP     XLRE      XLU      XLV      XLY  Daily Total
Date                                                                                                                      
2018-06-29      NaN  16658.9  4208.96  33514.7     2247  17012.9  336.696  7915.74  5249.41  2283.92  10571.7    100000.00
2018-07-02      NaN  16783.5  4140.82    33704  2250.76  17177.1  334.866  7872.18  5288.83  2291.04  10587.2    100430.23
2018-07-03      NaN  16564.3  4175.16  33388.6  2244.49  16973.7  335.716  7915.74  5303.99  2298.16    10533     99732.87
2018-07-05      NaN  16830.7   4166.3  33476.9  2254.84  17211.4  340.422   8019.8  5335.32   2321.7  10587.2    100544.48
2018-07-06      NaN  17096.7  4192.34  33628.3  2262.99  17409.9  341.403  8051.26  5374.74  2354.54  10670.3    101382.47
2018-07-09      NaN  17197.7  4254.93  34422.9  2304.39  17544.6  339.899  7978.66  5207.98  2370.15  10797.1    102418.38
2018-07-10      NaN  17187.3  4286.51  34271.6  2311.92  17591.2  344.083  8017.38  5258.51  2380.27  10819.3    102468.05
2018-07-11      NaN  17164.1     4194  34107.6  2274.91  17500.5  342.906  7990.76     5305  2361.11  10796.1    102036.97
2018-07-12      NaN  17433.5   4201.2  34170.7     2300  17794.6  342.579  8010.12  5308.03  2388.21  10867.7    102816.52
2018-07-13      NaN  17406.5  4224.19  34006.7   2313.8  17779.9  344.671  7988.34  5311.07  2393.41  10893.8    102662.35
2018-07-16      NaN    17356  4174.61  34631.1  2303.77  17730.9  343.037  7942.36  5303.99  2377.26    10916    103079.01
2018-07-17      NaN    17356  4160.76  34687.8  2312.71  17863.2  345.913  7891.54  5300.96  2390.68  10927.6    103237.22
2018-07-18      NaN  17308.9  4161.87  35217.6  2338.58  17838.7  343.429  7857.66  5273.67  2392.32  10918.9    103651.62
2018-07-19      NaN  17187.6  4161.87  34700.4  2337.64  17778.6  343.494  7936.31  5323.19  2379.18  10896.7    103045.10
2018-07-20      NaN  17130.4  4147.47  34776.1  2334.82  17777.4  345.455  7864.92  5283.78  2374.25  10848.3    102882.95
2018-07-23      NaN  17187.6  4130.85  35230.2  2320.23  17863.2  343.494  7845.56   5248.4     2380  10837.7    103387.27
2018-07-24      NaN  17322.3  4182.92  35331.1  2331.05  17963.6  343.952  7818.94  5265.59  2401.35  10805.8    103766.68
2018-07-25      NaN  17446.9   4221.7  35438.3  2363.36  18184.2   346.37  7896.38  5280.75  2429.54  10884.1    104491.67
2018-07-26      NaN    16789  4264.35  35387.9  2383.43  17909.7  348.527  7924.21  5340.37  2424.62  10826.1    103598.22
2018-07-27      NaN  16470.4  4244.96  35482.5  2383.12  17598.5   348.92  7852.82  5320.16   2407.1  10800.9    102909.41
2018-07-30      NaN  16221.2  4282.08  35495.1  2360.85  17333.9  348.527  7847.98  5288.83  2409.56  10715.8    102303.82
2018-07-31      NaN  16318.8  4268.78  35255.4  2410.72  17375.6  350.096   7995.6  5343.41  2433.92  10762.2    102514.60
2018-08-01      NaN  16251.5  4211.73  35255.4   2380.3  17529.9  347.024  8053.68  5299.95  2435.02  10713.9    102478.42
2018-08-02      NaN  16359.2  4189.57  35268.1  2376.53  17750.5  350.782  8010.12  5329.26   2443.5  10780.6    102858.14
2018-08-03      NaN  16470.4  4169.07  35457.3  2378.42  17816.6  354.933  8115.39  5384.84  2458.56  10816.4    103421.87
2018-08-06      NaN  16625.3  4184.58  35633.9  2381.71    17922  354.999  8098.45  5391.92  2462.39  10890.9    103946.05
2018-08-07      NaN  16652.2  4213.94  35797.8   2398.8  17983.2  352.972  8085.14  5381.81  2462.39  10940.2    104268.57
2018-08-08      NaN  16642.1  4183.47  35898.7  2388.45  18029.8  350.292  8036.74  5354.52  2466.22  10953.8    104304.13
2018-08-09      NaN    16733  4144.14  35709.5  2375.59  18037.2  349.312  8048.84  5377.77  2463.49  10994.4    104233.26
2018-08-10      NaN  16591.6  4167.41  35293.3  2356.46  17897.5   348.07  7968.98  5355.53  2453.63  10902.5    103334.95
2018-08-13      NaN    16568  4116.44  34940.1  2344.54  17875.4  347.939  7968.

In [18]:
dollar_value.to_csv("SOROS_dollar_value.csv")
etf_portfolio.to_csv("SOROS_etf_portfolio.csv")
portfolio_value.to_csv("SOROS_portfolio_value.csv")

In [16]:
portfolio_daily_return = portfolio_value.pct_change()
portfolio_daily_return

XLB       XLC       XLE       XLF       XLI       XLK        XLP      XLRE       XLU       XLV       XLY   Daily Total
Date                                                                                                                                    
2018-06-29        NaN       NaN       NaN       NaN       NaN       NaN        NaN       NaN       NaN       NaN       NaN           NaN
2018-07-02        NaN  0.007479 -0.016188  0.005645  0.001675  0.009650  -0.005436 -0.005503  0.007509  0.003116  0.001464  4.302300e-03
2018-07-03        NaN -0.013062  0.008294 -0.009356 -0.002787 -0.011840   0.002538  0.005533  0.002866  0.003106 -0.005116 -6.943726e-03
2018-07-05        NaN  0.016079 -0.002123  0.002645  0.004612  0.014003   0.014019  0.013146  0.005907  0.010243  0.005143  8.137839e-03
2018-07-06        NaN  0.015808  0.006249  0.004521  0.003617  0.011532   0.002880  0.003923  0.007388  0.014148  0.007857  8.334520e-03
2018-07-09        NaN  0.005909  0.014931  0.023631  0.018295  0.007741  -0.004404 -0.009017 -0.031027  0.006626  0.011876  1.021784e-02
2018-07-10        NaN -0.000607  0.007421 -0.004397  0.003267  0.002654   0.012308  0.004853  0.009703  0.004273  0.002061  4.849715e-04
2018-07-11        NaN -0.001352 -0.021582 -0.004785 -0.016009 -0.005154  -0.003419 -0.003320  0.008841 -0.008050 -0.002146 -4.206970e-03
2018-07-12        NaN  0.015696  0.001717  0.001849  0.011030  0.016802  -0.000953  0.002423  0.000572  0.011477  0.006630  7.639878e-03
2018-07-13        NaN -0.001545  0.005472 -0.004799  0.006000 -0.000826   0.006106 -0.002719  0.000571  0.002178  0.002403 -1.499467e-03
2018-07-16        NaN -0.002902 -0.011737  0.018361 -0.004338 -0.002756  -0.004741 -0.005756 -0.001332 -0.006747  0.002042  4.058547e-03
2018-07-17        NaN  0.000000 -0.003317  0.001639  0.003880  0.007463   0.008384 -0.006399 -0.000572  0.005642  0.001063  1.534842e-03
2018-07-18        NaN -0.002716  0.000266  0.015273  0.011189 -0.001372  -0.007181 -0.004293 -0.005148  0.000687 -0.000797  4.014056e-03
2018-07-19        NaN -0.007004  0.000000 -0.014685 -0.000402 -0.003365   0.000190  0.010009  0.009391 -0.005492 -0.002038 -5.851525e-03
2018-07-20        NaN -0.003331 -0.003461  0.002181 -0.001208 -0.000069   0.005709 -0.008995 -0.007405 -0.002071 -0.004439 -1.573583e-03
2018-07-23        NaN  0.003342 -0.004007  0.013058 -0.006247  0.004824  -0.005676 -0.002462 -0.006695  0.002421 -0.000981  4.901881e-03
2018-07-24        NaN  0.007837  0.012606  0.002864  0.004664  0.005624   0.001332 -0.003393  0.003274  0.008971 -0.002945  3.669794e-03
2018-07-25        NaN  0.007193  0.009270  0.003035  0.013859  0.012277   0.007032  0.009904  0.002879  0.011741  0.007251  6.986732e-03
2018-07-26        NaN -0.037711  0.010104 -0.001424  0.008494 -0.015092   0.006228  0.003524  0.011292 -0.002028 -0.005332 -8.550442e-03
2018-07-27        NaN -0.018979 -0.004547  0.002673 -0.000132 -0.017376   0.001125 -0.009009 -0.003785 -0.007225 -0.002323 -6.648859e-03
2018-07-30        NaN -0.015130  0.008743  0.000355 -0.009345 -0.015038  -0.001124 -0.000616 -0.005889  0.001023 -0.007881 -5.884690e-03
2018-07-31        NaN  0.006020 -0.003105 -0.006752  0.021124  0.002403   0.004501  0.018810  0.010319  0.010110  0.004333  2.060334e-03
2018-08-01        NaN -0.004127 -0.013366  0.000000 -0.012620  0.008885  -0.008775  0.007264 -0.008133  0.000450 -0.004494 -3.529253e-04
2018-08-02        NaN  0.006631 -0.005261  0.000358 -0.001581  0.012580   0.010831 -0.005409  0.005530  0.003485  0.006230  3.705365e-03
2018-08-03        NaN  0.006793 -0.004892  0.005365  0.000792  0.003727   0.011833  0.013142  0.010430  0.006161  0.003320  5.480655e-03
2018-08-06        NaN  0.009405  0.003720  0.004980  0.001385  0.005914   0.000184 -0.002087  0.001314  0.001559  0.006886  5.068367e-03
2018-08-07        NaN  0.001620  0.007016  0.004602  0.007177  0.003418  -0.005708 -0.001644 -0.001874  0.000000  0.004530  3.102763e-03
2018-08-08        NaN -0.000607 -0.007230  0.

In [17]:
cumulative_portfolio_return = (1 + portfolio_daily_return).cumprod().dropna()
cumulative_portfolio_return

XLB       XLC       XLE       XLF       XLI       XLK        XLP      XLRE       XLU       XLV       XLY  Daily Total
Date                                                                                                                                  
2019-01-02  1.009365  1.300759  0.714798  0.557804  0.156632  0.753456  20.815546  1.313282  0.887768  0.305780  0.912955     0.898723
2019-01-03  0.983999  1.281772  0.708868  0.547638  0.152376  0.717445  20.724811  1.321096  0.891186  0.300072  0.895455     0.883963
2019-01-04  1.021109  1.335309  0.732715  0.564674  0.158001  0.747557  21.110437  1.334120  0.901698  0.308473  0.924042     0.911276
2019-01-07  1.024589  1.351495  0.743293  0.566071  0.159250  0.755039  21.108374  1.345408  0.896314  0.309947  0.945712     0.919147
2019-01-08  1.034040  1.373750  0.749163  0.565721  0.161432  0.760939  21.310467  1.368852  0.907595  0.312409  0.954966     0.928286
2019-01-09  1.034338  1.374528  0.759925  0.568166  0.162439  0.770429  21.100126  1.363208  0.900587  0.313284  0.959410     0.930295
2019-01-10  1.044386  1.377796  0.762860  0.569331  0.164851  0.774018  21.227980  1.385566  0.914261  0.314181  0.957302     0.934825
2019-01-11  1.039213  1.370170  0.757846  0.569913  0.164524  0.772680  21.281638  1.385783  0.909133  0.315007  0.957806     0.933257
2019-01-14  1.031433  1.366435  0.757112  0.574337  0.164584  0.766353  21.194986  1.384155  0.888879  0.312045  0.953179     0.930901
2019-01-15  1.025086  1.387290  0.758335  0.578645  0.163930  0.776816  21.388830  1.399238  0.900929  0.316952  0.960738     0.940968
2019-01-16  1.029662  1.381998  0.758641  0.592034  0.164245  0.777911  21.271286  1.406622  0.903151  0.316695  0.958448     0.944879
2019-01-17  1.046376  1.387445  0.765673  0.594942  0.166900  0.782778  21.370270  1.412266  0.906740  0.319710  0.964632     0.949787
2019-01-18  1.062890  1.398495  0.780226  0.604725  0.169943  0.793849  21.603295  1.415739  0.906997  0.322942  0.978010     0.960182
2019-01-22  1.046575  1.365813  0.761882  0.596691  0.166076  0.778520  21.376457  1.412917  0.908706  0.320177  0.961425     0.945716
2019-01-23  1.042396  1.362700  0.755706  0.598438  0.166718  0.783508  21.669285  1.414871  0.919047  0.321326  0.964907     0.948426
2019-01-24  1.036925  1.371415  0.759925  0.600349  0.167821  0.791477  21.407389  1.422469  0.924345  0.318956  0.970313     0.952542
2019-01-25  1.057319  1.387912  0.768975  0.604957  0.169894  0.801818  21.341400  1.437881  0.911099  0.319064  0.980025     0.960538
2019-01-28  1.055130  1.375617  0.761393  0.603095  0.168209  0.791112  21.413576  1.451990  0.906569  0.315402  0.974070     0.956076
2019-01-29  1.066073  1.359121  0.764449  0.601465  0.170488  0.783204  21.452757  1.463061  0.908877  0.316982  0.968206     0.952261
2019-01-30  1.078310  1.378263  0.774967  0.604026  0.173216  0.807171  21.609482  1.476953  0.916226  0.321263  0.987172     0.965117
2019-01-31  1.061597  1.435846  0.779492  0.604957  0.174089  0.806502  22.073470  1.491931  0.938275  0.326101  0.997297     0.980053
2019-02-01  1.065278  1.430711  0.792822  0.606704  0.174368  0.810943  21.943553  1.481078  0.932208  0.325885  0.981995     0.977901
2019-02-04  1.062592  1.442383  0.795268  0.609149  0.176489  0.823322  22.071408  1.489305  0.933575  0.324611  0.987906     0.984646
2019-02-05  1.069854  1.459191  0.795512  0.607985  0.178065  0.831017  22.094092  1.499746  0.935455  0.324557  0.997343     0.990475
2019-02-06  1.063785  1.428065  0.790498  0.607053  0.178041  0.833755  22.110589  1.488024  0.934857  0.325706  0.993494     0.983892
2019-02-07  1.048564  1.410946  0.773133  0.600650  0.176768  0.821345  22.061097  1.499529  0.946565  0.322044  0.984652     0.976226
2019-02-08  1.047370  1.421062  0.768547  0.597157  0.176853  0.825177  22.147708  1.500397  0.951009  0.322439  0.980117     0.977314
2019-02-11  1.049957  1.408455  0.773622  0.599602  0.178138  0.826759  22.238403  1.504087  0.951094 